In [1]:
# Modelos de Detección de Outliers
import plotly.graph_objects as go
import pandas as pd
import numpy as np

pd.set_option('display.max_columns', None)

from sklearn.preprocessing import StandardScaler, RobustScaler, MinMaxScaler
from sklearn.neighbors import LocalOutlierFactor
from sklearn.ensemble import IsolationForest

import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping

In [7]:
# Función para graficar resultados
def plot_anomalies(df, title, model_name):
    """
    Grafica los resultados de detección de anomalías
    
    Parámetros:
    - df: DataFrame con columnas 'Fecha', 'Volumen' y 'anomaly'
    - title: Título del gráfico
    - model_name: Nombre del modelo para el subtítulo
    """
    fig = go.Figure()
    
    # Puntos normales
    fig.add_trace(
        go.Scatter(
            x=df[df['anomaly'] == 0]['Fecha'],
            y=df[df['anomaly'] == 0]['Volumen'],
            mode='markers',
            name='Normal',
            marker=dict(color='blue', size=6, opacity=0.7)
        )
    )
    
    # Puntos anómalos
    fig.add_trace(
        go.Scatter(
            x=df[df['anomaly'] == 1]['Fecha'],
            y=df[df['anomaly'] == 1]['Volumen'],
            mode='markers',
            name='Anomalía',
            marker=dict(color='red', size=8, symbol='x')
        )
    )
    
    # # Línea de tendencia
    # fig.add_trace(
    #     go.Scatter(
    #         x=df['Fecha'],
    #         y=df['Volumen'].rolling(24, min_periods=1).mean(),
    #         mode='lines',
    #         name='Media móvil 24h',
    #         line=dict(color='green', width=2)
    #     )
    # )
    
    fig.update_layout(
        title=f'{title} - Cliente 1<br><sup>Modelo: {model_name}</sup>',
        xaxis_title='Fecha',
        yaxis_title='Volumen',
        legend_title='Leyenda',
        template='plotly_white',
        hovermode='x unified',
        height=600
    )
    
    fig.show()

In [8]:
# Cargar datos del cliente 1
data_cliente1 = pd.read_csv("../data/processed/CLIENTE1.csv", parse_dates=['Fecha'])

# Calcular contaminación (proporción de outliers)
contamination = data_cliente1['is_any_outlier'].sum() / len(data_cliente1)
print(f"Proporción de outliers en datos originales: {contamination:.4f}")

# Eliminar columnas de outliers existentes
data = data_cliente1.drop(['Volumen_outlier_zscore', 'is_any_outlier', 'Volumen_outlier_iqr'], axis=1)

Proporción de outliers en datos originales: 0.0001


In [9]:
# 1. ISOLATION FOREST
def detect_with_isolation_forest(data, contamination=0.025):
    """Detección de anomalías con Isolation Forest"""
    df = data.copy()
    
    # Preparar datos
    df_iso = df.drop(["Cliente", "Fecha"], axis=1)
    df_iso = df_iso.replace([np.inf, -np.inf], np.nan).ffill()
    
    # Escalar datos
    scaler = RobustScaler()
    X = scaler.fit_transform(df_iso)
    
    # Entrenar modelo
    clf = IsolationForest(n_estimators=250, contamination=contamination, random_state=42)
    df["anomaly"] = clf.fit_predict(X)
    df["anomaly"] = df["anomaly"].map({1: 0, -1: 1})  # Convertir a 0=normal, 1=anomalía
    
    return df

# Aplicar Isolation Forest
iso_data = detect_with_isolation_forest(data)
plot_anomalies(iso_data, "Detección de Anomalías", "Isolation Forest")

In [10]:
# 2. AUTOENCODER
def detect_with_autoencoder(data, threshold_percentile=85):
    """Detección de anomalías con Autoencoder"""
    df = data.copy()
    
    # Preparar datos
    df_ae = df.drop(["Cliente", "Fecha"], axis=1)
    df_ae = df_ae.replace([np.inf, -np.inf], np.nan).ffill()
    
    # Escalar datos
    scaler = MinMaxScaler()
    X = scaler.fit_transform(df_ae)
    
    # Construir y entrenar autoencoder
    autoencoder = build_autoencoder(X.shape[1])
    early_stop = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
    
    history = autoencoder.fit(
        X, X,
        epochs=100,
        batch_size=32,
        validation_split=0.2,
        callbacks=[early_stop],
        verbose=0
    )
    
    # Predecir reconstrucciones
    reconstructions = autoencoder.predict(X)
    mse = np.mean(np.power(X - reconstructions, 2), axis=1)
    
    # Determinar umbral
    threshold = np.percentile(mse, threshold_percentile)
    df["anomaly"] = np.where(mse > threshold, 1, 0)
    
    return df

# Función para construir el autoencoder (ya definida en tu código)
def build_autoencoder(input_dim, encoding_dim=16):
    # Encoder
    input_layer = Input(shape=(input_dim,))
    encoder = Dense(encoding_dim, activation='relu')(input_layer)
    encoder = Dropout(0.1)(encoder)
    
    # Decoder
    decoder = Dense(input_dim, activation='linear')(encoder)
    
    # Autoencoder
    autoencoder = Model(inputs=input_layer, outputs=decoder)
    autoencoder.compile(optimizer=Adam(learning_rate=0.001), loss='mse')
    
    return autoencoder

# Aplicar Autoencoder
ae_data = detect_with_autoencoder(data)
plot_anomalies(ae_data, "Detección de Anomalías", "Autoencoder")

1360/1360 ━━━━━━━━━━━━━━━━━━━━ 1s 525us/step


In [6]:
# 3. LOCAL OUTLIER FACTOR (LOF)
def detect_with_lof(data, contamination=0.025):
    """Detección de anomalías con Local Outlier Factor"""
    df = data.copy()
    
    # Preparar datos - más robusto para manejar NaNs
    df_lof = df.drop(["Cliente", "Fecha"], axis=1)
    
    # 1. Reemplazar infinitos por NaN
    df_lof = df_lof.replace([np.inf, -np.inf], np.nan)
    
    # 2. Eliminar filas con demasiados NaNs (opcional)
    # df_lof = df_lof.dropna(thresh=len(df_lof.columns)-3)  # Mantener filas con al menos n-3 valores válidos
    
    # 3. Imputación de valores faltantes
    from sklearn.impute import SimpleImputer
    imputer = SimpleImputer(strategy='median')  # Puedes usar 'mean' o 'median'
    X_imputed = imputer.fit_transform(df_lof)
    
    # Escalar datos
    scaler = StandardScaler()
    X = scaler.fit_transform(X_imputed)
    
    # Entrenar modelo
    lof = LocalOutlierFactor(
        n_neighbors=20, 
        contamination=contamination,
        novelty=False  # Asegurarse que estamos en modo detección de outliers
    )
    
    # Predecir anomalías
    y_pred = lof.fit_predict(X)
    
    # Crear DataFrame resultante manteniendo solo las filas que no fueron eliminadas
    result_df = df.copy()
    result_df["anomaly"] = np.nan  # Inicializar con NaN
    
    # Asignar predicciones (convertir -1=anomalía a 1, 1=normal a 0)
    result_df.loc[df_lof.notna().all(axis=1), "anomaly"] = np.where(y_pred == -1, 1, 0)
    
    return result_df

# Aplicar LOF corregido
lof_data = detect_with_lof(data)
plot_anomalies(lof_data, "Detección de Anomalías", "Local Outlier Factor (LOF)")

# Aplicar LOF
lof_data = detect_with_lof(data)
plot_anomalies(lof_data, "Detección de Anomalías", "Local Outlier Factor")

ValueError: Must have equal len keys and value when setting with an iterable